<a href="https://colab.research.google.com/github/shruthad/Fake-news-detection/blob/main/FAKE_NEWS_DETECTION.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import pandas as pd
import nltk
from nltk.corpus import stopwords
from nltk.stem.porter import PorterStemmer
from sklearn.metrics import classification_report,confusion_matrix,accuracy_score
from sklearn.model_selection import train_test_split
from string import punctuation
import keras
from keras.models import Sequential
from keras.layers import Dense
import tensorflow as tf
from tensorflow.keras.layers import Embedding
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential
from tensorflow.keras.preprocessing.text import one_hot
from tensorflow.keras.layers import LSTM
from tensorflow.keras.layers import Dense

In [ ]:
true['category'] = 1
false['category'] = 0

In [ ]:

true=pd.read_csv('True.csv')
false=pd.read_csv('Fake.csv')


In [ ]:
df = pd.concat([true,false])

In [ ]:
df.title.count()

44898

In [ ]:
df.subject.value_counts()

politicsNews       11272
worldnews          10145
News                9050
politics            6841
left-news           4459
Government News     1570
US_News              783
Middle-east          778
Name: subject, dtype: int64

In [ ]:
df['text'] = df['text'] + " " + df['title'] + " " + df['subject']
del df['title']
del df['subject']
del df['date']

In [ ]:
df

text  category
0      WASHINGTON (Reuters) - The head of a conservat...         1
1      WASHINGTON (Reuters) - Transgender people will...         1
2      WASHINGTON (Reuters) - The special counsel inv...         1
3      WASHINGTON (Reuters) - Trump campaign adviser ...         1
4      SEATTLE/WASHINGTON (Reuters) - President Donal...         1
...                                                  ...       ...
23476  21st Century Wire says As 21WIRE reported earl...         0
23477  21st Century Wire says It s a familiar theme. ...         0
23478  Patrick Henningsen  21st Century WireRemember ...         0
23479  21st Century Wire says Al Jazeera America will...         0
23480  21st Century Wire says As 21WIRE predicted in ...         0

[44898 rows x 2 columns]

In [ ]:
import nltk
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


True

In [ ]:
stop = set(stopwords.words('english'))
punctuation = list(string.punctuation)
stop.update(punctuation)

In [ ]:
stemmer = PorterStemmer()
def stem_text(text):
    final_text = []
    for i in text.split():
        if i.strip().lower() not in stop:
            word = stemmer.stem(i.strip())
            final_text.append(word)
    return " ".join(final_text)  

In [ ]:
df.text = df.text.apply(stem_text)

In [ ]:
df.text

0        washington (reuters) head conserv republican f...
1        washington (reuters) transgend peopl allow fir...
2        washington (reuters) special counsel investig ...
3        washington (reuters) trump campaign advis geor...
4        seattle/washington (reuters) presid donald tru...
                               ...                        
23476    21st centuri wire say 21wire report earlier we...
23477    21st centuri wire say familiar theme. whenev d...
23478    patrick henningsen 21st centuri wirerememb oba...
23479    21st centuri wire say Al jazeera america go hi...
23480    21st centuri wire say 21wire predict new year ...
Name: text, Length: 44898, dtype: object

In [ ]:
df.text[0]

0    washington (reuters) head conserv republican f...
0    donald trump wish american happi new year leav...
Name: text, dtype: object

In [ ]:
voc_size=5000
onehot_repr=[one_hot(words,voc_size)for words in df.text] 
onehot_repr

[[1550,
  3795,
  883,
  891,
  3239,
  675,
  1026,
  3573,
  1079,
  43,
  3512,
  4058,
  2428,
  4779,
  4795,
  401,
  302,
  3645,
  123,
  3664,
  1194,
  4703,
  2404,
  3370,
  4670,
  2121,
  3344,
  1701,
  1846,
  4923,
  210,
  3566,
  1026,
  3573,
  2001,
  3172,
  2752,
  3563,
  4710,
  1711,
  4779,
  3621,
  154,
  893,
  1639,
  1089,
  2072,
  3839,
  3130,
  2702,
  2562,
  4741,
  4864,
  2461,
  3839,
  1671,
  3659,
  913,
  1089,
  3370,
  3181,
  4018,
  984,
  2854,
  4288,
  2080,
  4587,
  3337,
  2972,
  4721,
  3836,
  4957,
  3239,
  4882,
  3344,
  1398,
  1079,
  3412,
  1518,
  4102,
  3239,
  4809,
  3094,
  3370,
  1027,
  4007,
  2072,
  2139,
  3753,
  4809,
  4141,
  1027,
  3092,
  4213,
  2403,
  3111,
  1059,
  4957,
  1220,
  1462,
  805,
  3466,
  4284,
  680,
  1203,
  2517,
  4922,
  4102,
  1916,
  1680,
  4198,
  2220,
  2750,
  4127,
  1027,
  3092,
  4213,
  3809,
  3111,
  4132,
  491,
  3896,
  2752,
  4887,
  993,
  100,
  3482,
  

In [ ]:
onehot_repr[0]

[1550,
 3795,
 883,
 891,
 3239,
 675,
 1026,
 3573,
 1079,
 43,
 3512,
 4058,
 2428,
 4779,
 4795,
 401,
 302,
 3645,
 123,
 3664,
 1194,
 4703,
 2404,
 3370,
 4670,
 2121,
 3344,
 1701,
 1846,
 4923,
 210,
 3566,
 1026,
 3573,
 2001,
 3172,
 2752,
 3563,
 4710,
 1711,
 4779,
 3621,
 154,
 893,
 1639,
 1089,
 2072,
 3839,
 3130,
 2702,
 2562,
 4741,
 4864,
 2461,
 3839,
 1671,
 3659,
 913,
 1089,
 3370,
 3181,
 4018,
 984,
 2854,
 4288,
 2080,
 4587,
 3337,
 2972,
 4721,
 3836,
 4957,
 3239,
 4882,
 3344,
 1398,
 1079,
 3412,
 1518,
 4102,
 3239,
 4809,
 3094,
 3370,
 1027,
 4007,
 2072,
 2139,
 3753,
 4809,
 4141,
 1027,
 3092,
 4213,
 2403,
 3111,
 1059,
 4957,
 1220,
 1462,
 805,
 3466,
 4284,
 680,
 1203,
 2517,
 4922,
 4102,
 1916,
 1680,
 4198,
 2220,
 2750,
 4127,
 1027,
 3092,
 4213,
 3809,
 3111,
 4132,
 491,
 3896,
 2752,
 4887,
 993,
 100,
 3482,
 4193,
 1046,
 3371,
 1059,
 3605,
 2139,
 2220,
 585,
 376,
 1927,
 3311,
 2991,
 401,
 1933,
 2459,
 4489,
 491,
 3861,
 1546,


In [ ]:
sent_length=500
embedded_docs=pad_sequences(onehot_repr,padding='pre',maxlen=sent_length)
print(embedded_docs)

[[   0    0    0 ... 3861 2627 3140]
 [   0    0    0 ...  336  409 3140]
 [   0    0    0 ... 1397 2023 3140]
 ...
 [2458 4221 2878 ... 4718 4788  530]
 [   0    0    0 ... 3605 4788  530]
 [3243  979 4886 ... 3481 4788  530]]


In [ ]:
embedded_docs[0]

array([   0,    0,    0,    0,    0,    0,    0,    0,    0, 1550, 3795,
        883,  891, 3239,  675, 1026, 3573, 1079,   43, 3512, 4058, 2428,
       4779, 4795,  401,  302, 3645,  123, 3664, 1194, 4703, 2404, 3370,
       4670, 2121, 3344, 1701, 1846, 4923,  210, 3566, 1026, 3573, 2001,
       3172, 2752, 3563, 4710, 1711, 4779, 3621,  154,  893, 1639, 1089,
       2072, 3839, 3130, 2702, 2562, 4741, 4864, 2461, 3839, 1671, 3659,
        913, 1089, 3370, 3181, 4018,  984, 2854, 4288, 2080, 4587, 3337,
       2972, 4721, 3836, 4957, 3239, 4882, 3344, 1398, 1079, 3412, 1518,
       4102, 3239, 4809, 3094, 3370, 1027, 4007, 2072, 2139, 3753, 4809,
       4141, 1027, 3092, 4213, 2403, 3111, 1059, 4957, 1220, 1462,  805,
       3466, 4284,  680, 1203, 2517, 4922, 4102, 1916, 1680, 4198, 2220,
       2750, 4127, 1027, 3092, 4213, 3809, 3111, 4132,  491, 3896, 2752,
       4887,  993,  100, 3482, 4193, 1046, 3371, 1059, 3605, 2139, 2220,
        585,  376, 1927, 3311, 2991,  401, 1933, 24

In [ ]:
embedding_vector_features=40
model=Sequential()
model.add(Embedding(voc_size,embedding_vector_features,input_length=sent_length))
model.add(LSTM(100))
model.add(Dense(1,activation='sigmoid'))
model.compile(loss='binary_crossentropy',optimizer='adam',metrics=['accuracy'])
print(model.summary())

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding (Embedding)        (None, 500, 40)           200000    
_________________________________________________________________
lstm (LSTM)                  (None, 100)               56400     
_________________________________________________________________
dense (Dense)                (None, 1)                 101       
Total params: 256,501
Trainable params: 256,501
Non-trainable params: 0
_________________________________________________________________
None


In [ ]:
len(embedded_docs),df.category

(44898, 0        1
 1        1
 2        1
 3        1
 4        1
         ..
 23476    0
 23477    0
 23478    0
 23479    0
 23480    0
 Name: category, Length: 44898, dtype: int64)

In [ ]:

import numpy as np
X_final=np.array(embedded_docs)
y_final=np.array(df.category)

In [ ]:

X_final.shape,y_final.shape

((44898, 500), (44898,))

In [ ]:

from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X_final, y_final, test_size=0.33,shuffle=True, random_state=42)

In [ ]:
model.fit(X_train,y_train,validation_split=0.2,epochs=10,batch_size=64)

Epoch 1/10
376/376 [==============================] - 48s 40ms/step - loss: 0.2514 - accuracy: 0.9063 - val_loss: 0.0037 - val_accuracy: 0.9998
Epoch 2/10
376/376 [==============================] - 14s 38ms/step - loss: 0.0014 - accuracy: 0.9999 - val_loss: 0.0013 - val_accuracy: 0.9998
Epoch 3/10
376/376 [==============================] - 14s 38ms/step - loss: 2.5197e-04 - accuracy: 1.0000 - val_loss: 0.0010 - val_accuracy: 0.9998
Epoch 4/10
376/376 [==============================] - 14s 38ms/step - loss: 9.2797e-05 - accuracy: 1.0000 - val_loss: 9.1704e-04 - val_accuracy: 0.9998
Epoch 5/10
376/376 [==============================] - 14s 38ms/step - loss: 4.2440e-05 - accuracy: 1.0000 - val_loss: 0.0011 - val_accuracy: 0.9998
Epoch 6/10
376/376 [==============================] - 14s 38ms/step - loss: 5.7112e-05 - accuracy: 1.0000 - val_loss: 0.0011 - val_accuracy: 0.9997
Epoch 7/10
376/376 [==============================] - 14s 38ms/step - loss: 3.6695e-05 - accuracy: 1.0000 - val_loss

In [ ]:
from tensorflow.keras.layers import Dropout
## Creating model
embedding_vector_features=40
model=Sequential()
model.add(Embedding(voc_size,embedding_vector_features,input_length=sent_length))
model.add(Dropout(0.3))
model.add(LSTM(100))
model.add(Dropout(0.3))
model.add(Dense(1,activation='sigmoid'))
model.compile(loss='binary_crossentropy',optimizer='adam',metrics=['accuracy'])

In [ ]:
y_pred=model.predict_classes(X_test)

/usr/local/lib/python3.7/dist-packages/tensorflow/python/keras/engine/sequential.py:450: UserWarning: `model.predict_classes()` is deprecated and will be removed after 2021-01-01. Please use instead:* `np.argmax(model.predict(x), axis=-1)`,   if your model does multi-class classification   (e.g. if it uses a `softmax` last-layer activation).* `(model.predict(x) > 0.5).astype("int32")`,   if your model does binary classification   (e.g. if it uses a `sigmoid` last-layer activation).
  warnings.warn('`model.predict_classes()` is deprecated and '


In [ ]:
from sklearn.metrics import confusion_matrix
confusion_matrix(y_test,y_pred)

array([[7716,    1],
       [   8, 7092]])

In [ ]:

from sklearn.metrics import accuracy_score
accuracy_score(y_test,y_pred)

0.999392589593035